# Backtest Functionality with Testing for using the old regression scorefile


In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import scipy.stats as stats
import datetime as dt
import itertools as it
import ast

import sys
sys.path.append('../src')
from utils import *

In [2]:
# Import the price data from "../Raw Data/ETF_PriceFile_2017_to_2025.csv"
df_price_all = pd.read_csv('../Raw Data/ETF_PriceFile_2017_to_2025.csv', index_col=0)

In [3]:
# Import the old score summary from "../Score Summary/df_score_summary_old_reg.csv"
df_score_summary_old = pd.read_csv('../Score Summary/df_score_summary_old_reg.csv')

In [4]:
# Create the "Combined Score" using the old_coefficient of 32 (days)
df_score_summary_old["Combined Score"] = df_score_summary_old["Cheapness"] + 32 * df_score_summary_old["Combined Term 2"]

# Generate the score_file using df_score_summary_old
df_scorefile = df_score_summary_old.pivot_table(index = "Date", columns = "Ticker", values = "Combined Score")

# Backtesting using the Old Score
<strong>Backtesting function</strong>
<ul>
<em>Portfolio_Tracker(df_scores, df_price, date_range, num_positions, swap_threshold, trade_threshold, initial_capital = 1000, trade_cost_assumption = 0.001)</em>
</ul>

<strong>Assumptions:-</strong>
<ul>
<li>num_positions = 8</li>
<li>swap_threshold = 0.015</li>
<li>trade_threshold = 0.0325</li>
<li>initial_capital = 1000</li>
<li>trade_cost_assumption = 0.0005 --> 5bps trading cost or 2.5bps on each side</li>
</ul>

In [5]:
# Drop the ARK ETFs from the df_scorefile

df_scorefile.drop(columns = ["ARKQ US Equity", "ARKG US Equity", "ARKK US Equity"], inplace = True, errors="ignore")
df_scorefile.head()

Ticker   ACWV US Equity  AGG US Equity  AMLP US Equity  ASHR US Equity  \
Date                                                                     
43097.0        0.009702      -0.000003       -0.001410        0.012742   
43098.0        0.009991      -0.000030        0.000505        0.011044   
43102.0        0.010395       0.000141       -0.002532        0.005519   
43103.0        0.009559       0.000290       -0.003080        0.003650   
43104.0        0.007177       0.000292        0.000742        0.004520   

Ticker   BBAX US Equity  BNDX US Equity  BOTZ US Equity  CALF US Equity  \
Date                                                                      
43097.0             NaN        0.003347        0.033652        0.016419   
43098.0             NaN        0.002874        0.034923        0.016768   
43102.0             NaN        0.003893        0.030376        0.013891   
43103.0             NaN        0.003252        0.022218        0.015967   
43104.0             NaN        0.002954        0.017602        0.014695   

Ticker   CIBR US Equity  COPX US Equity  ...  XLE US Equity  XLF US Equity  \
Date                                     ...                                 
43097.0        0.010882        0.018723  ...       0.011094       0.022570   
43098.0        0.012426        0.022789  ...       0.014558       0.026999   
43102.0        0.008386        0.024830  ...       0.009721       0.028273   
43103.0        0.005120        0.028673  ...       0.004969       0.024831   
43104.0        0.004781        0.027095  ...       0.005737       0.019602   

Ticker   XLI US Equity  XLK US Equity  XLP US Equity  XLU US Equity  \
Date                                                                  
43097.0       0.016078       0.027164       0.015123      -0.009214   
43098.0       0.018490       0.028925       0.014820      -0.009994   
43102.0       0.017349       0.022926       0.017740      -0.009060   
43103.0       0.015260       0.018409       0.016646      -0.009004   
43104.0       0.012038       0.016237       0.014624      -0.009998   

Ticker   XLV US Equity  XLY US Equity  XME US Equity  XOP US Equity  
Date                                                                 
43097.0       0.005483       0.023628       0.022125       0.014019  
43098.0       0.006578       0.028090       0.025257       0.021814  
43102.0       0.003932       0.019816       0.017766       0.012943  
43103.0       0.001156       0.018910       0.025010       0.012435  
43104.0       0.001573       0.018961       0.025334       0.014211  

[5 rows x 89 columns]

In [6]:
# Date range for the backtest would be the range of dates in df_scorefile
date_range = df_scorefile.index

# Holdings throughout the date_range
# Current Backtest assumptions:


df_portfolio_backtest_old = Portfolio_Tracker(df_scorefile, df_price_all, date_range, 8, 0.015, 0.0325, 1000, 0.0005)

z:\Section-A\Friedenthal Financial\Research and Models\Tactical Trend\Tactical Model Charlie\ETF Model 2025\Organized Folder\notebooks\../src\utils.py:151: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_max_swaps["Existing Ticker"] = df_held_scores["Ticker"]
z:\Section-A\Friedenthal Financial\Research and Models\Tactical Trend\Tactical Model Charlie\ETF Model 2025\Organized Folder\notebooks\../src\utils.py:152: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_max_swaps["Current Score"] = df_held_scores[cu

In [7]:
# View Results (Results have daily frequency)

start_date = df_portfolio_backtest_old.index[0]
end_date = df_portfolio_backtest_old.index[-1]

# Benchmark Results with VOO and Universe Mean

df_results = df_portfolio_backtest_old[["Return %", "Return % adjusted for swaps"]].copy()

df_perf = backtest_benchmarks(df_results, df_price_all, 1, start_date, end_date)
display(df_perf)

Start Date:  2017-12-29 00:00:00
End Date:  2025-03-12 00:00:00


Annualized Return  Standard Deviation  \
Group                                                                
Return %                                  1.84               22.10   
Return % adjusted for swaps               1.51               22.10   
Universe Mean                             7.68               18.04   
S&P 500                                  12.56               19.58   

                             Downside Deviation  Max Drawdown  
Group                                                          
Return %                                  17.17        -38.62  
Return % adjusted for swaps               17.18        -39.02  
Universe Mean                             14.75        -35.56  
S&P 500                                   16.15        -34.01

In [8]:
# Backtest Results (5 tickers --> VOO, IJH, IJR, VWO, VEA)

# Pick Top 1 out of 5; No Swap or Trade threshold; 5bp trading cost

tickers_5_list = ["VOO US Equity", "IJH US Equity", "IJR US Equity", "VWO US Equity", "VEA US Equity"]
df_portfolio_backtest_old_5 = Portfolio_Tracker(df_scorefile[tickers_5_list], df_price_all, date_range, 1, 0.0, 0.0, 1000, 0.0005)

z:\Section-A\Friedenthal Financial\Research and Models\Tactical Trend\Tactical Model Charlie\ETF Model 2025\Organized Folder\notebooks\../src\utils.py:151: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_max_swaps["Existing Ticker"] = df_held_scores["Ticker"]
z:\Section-A\Friedenthal Financial\Research and Models\Tactical Trend\Tactical Model Charlie\ETF Model 2025\Organized Folder\notebooks\../src\utils.py:152: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_max_swaps["Current Score"] = df_held_scores[cu

In [9]:
# View Results (Results have daily frequency)

start_date = df_portfolio_backtest_old_5.index[0]
end_date = df_portfolio_backtest_old_5.index[-1]

# Benchmark Results with VOO and Universe Mean

df_results_5 = df_portfolio_backtest_old_5[["Return %", "Return % adjusted for swaps"]].copy()

df_perf_5 = backtest_benchmarks(df_results_5, df_price_all[tickers_5_list], 1, start_date, end_date)
display(df_perf_5)

Start Date:  2017-12-29 00:00:00
End Date:  2025-03-12 00:00:00


Annualized Return  Standard Deviation  \
Group                                                                
Return %                                  7.00               20.86   
Return % adjusted for swaps               5.20               20.84   
Universe Mean                             7.11               19.54   
S&P 500                                  12.56               19.58   

                             Downside Deviation  Max Drawdown  
Group                                                          
Return %                                  16.90        -37.40  
Return % adjusted for swaps               16.89        -39.01  
Universe Mean                             15.84        -37.21  
S&P 500                                   16.15        -34.01

In [10]:
display(revert_Excel_Date(43097))
display(revert_Excel_Date(45289))

'2017-12-28'

'2023-12-29'

In [11]:
# Benchmark results for Sample period for new scores

df_perf_new_train_sample = backtest_benchmarks(df_results, df_price_all, 1, '2017-12-28', '2023-12-29')

Start Date:  2017-12-28
End Date:  2023-12-29


In [12]:
df_perf_new_train_sample

Annualized Return  Standard Deviation  \
Group                                                                
Return %                                  3.61               22.77   
Return % adjusted for swaps               3.28               22.77   
Universe Mean                             7.80               19.02   
S&P 500                                  11.97               20.62   

                             Downside Deviation  Max Drawdown  
Group                                                          
Return %                                  17.78        -38.62  
Return % adjusted for swaps               17.79        -39.02  
Universe Mean                             15.61        -35.56  
S&P 500                                   17.00        -34.01

In [17]:
"""
df_perf_new_train_sample.loc[["Universe Mean", "S&P 500"]].to_csv("../Result_New_Variations/Benchmarks_Performance_Train_Sample.csv")

"""

'\ndf_perf_new_train_sample.loc[["Universe Mean", "S&P 500"]].to_csv("../Result_New_Variations/Benchmarks_Performance_Train_Sample.csv")\n\n'